# Data Preparation

### Setting up the Kaggle API in Jupyter Notebook

In [ ]:
# Loads the API key
import os
import json

# Load Kaggle API credentials
with open('C:/Users/user/.kaggle/kaggle.json', 'r') as f:
    kaggle_creds = json.load(f)

# Set Kaggle API credentials as environment variables
os.environ['KAGGLE_USERNAME'] = kaggle_creds['username']
os.environ['KAGGLE_KEY'] = kaggle_creds['key']

In [15]:
# Download the dataset
!kaggle datasets download -d mohammadhossein77/brain-tumors-dataset

# Unzip the dataset
import zipfile
with zipfile.ZipFile('brain-tumors-dataset.zip', 'r') as zip_ref:
    zip_ref.extractall('brain_tumors_dataset')

Dataset URL: https://www.kaggle.com/datasets/mohammadhossein77/brain-tumors-dataset
License(s): CC0-1.0




  0%|          | 0.00/221M [00:00<?, ?B/s]
  0%|          | 1.00M/221M [00:01<04:27, 864kB/s]
  1%|          | 2.00M/221M [00:01<02:48, 1.37MB/s]
  1%|1         | 3.00M/221M [00:02<02:17, 1.66MB/s]
  2%|1         | 4.00M/221M [00:02<01:49, 2.08MB/s]
  2%|2         | 5.00M/221M [00:02<01:43, 2.19MB/s]
  3%|2         | 6.00M/221M [00:03<01:43, 2.19MB/s]
  3%|3         | 7.00M/221M [00:03<01:36, 2.32MB/s]
  4%|3         | 8.00M/221M [00:04<01:34, 2.36MB/s]
  4%|4         | 9.00M/221M [00:04<01:47, 2.07MB/s]
  5%|4         | 10.0M/221M [00:05<01:52, 1.96MB/s]
  5%|4         | 11.0M/221M [00:05<01:40, 2.20MB/s]
  5%|5         | 12.0M/221M [00:06<01:34, 2.33MB/s]
  6%|5         | 13.0M/221M [00:06<01:36, 2.27MB/s]
  6%|6         | 14.0M/221M [00:06<01:25, 2.54MB/s]
  7%|6         | 15.0M/221M [00:07<01:22, 2.63MB/s]
  7%|7         | 16.0M/221M [00:07<01:26, 2.48MB/s]
  8%|7         | 17.0M/221M [00:08<01:28, 2.42MB/s]
  8%|8         | 18.0M/221M [00:08<01:41, 2.09MB/s]
  9%|8         | 19.0

### Split the dataset to training, validation, and testing dataset

In [24]:
# Reorganize Directories
import os
import shutil

# Define the current and new directory paths
current_dir = 'brain_tumors_dataset/Data'
new_dir = 'dataset'

# Create new directories
os.makedirs(os.path.join(new_dir, 'normal'), exist_ok=True)
os.makedirs(os.path.join(new_dir, 'glioma'), exist_ok=True)
os.makedirs(os.path.join(new_dir, 'meningioma'), exist_ok=True)
os.makedirs(os.path.join(new_dir, 'pituitary'), exist_ok=True)

# Move normal images
normal_dir = os.path.join(current_dir, 'Normal')
for filename in os.listdir(normal_dir):
    src = os.path.join(normal_dir, filename)
    dst = os.path.join(new_dir, 'normal', filename)
    shutil.move(src, dst)

# Move glioma images
glioma_dir = os.path.join(current_dir, 'Tumor', 'glioma_tumor')
for filename in os.listdir(glioma_dir):
    src = os.path.join(glioma_dir, filename)
    dst = os.path.join(new_dir, 'glioma', filename)
    shutil.move(src, dst)

# Move meningioma images
meningioma_dir = os.path.join(current_dir, 'Tumor', 'meningioma_tumor')
for filename in os.listdir(meningioma_dir):
    src = os.path.join(meningioma_dir, filename)
    dst = os.path.join(new_dir, 'meningioma', filename)
    shutil.move(src, dst)

# Move pituitary images
pituitary_dir = os.path.join(current_dir, 'Tumor', 'pituitary_tumor')
for filename in os.listdir(pituitary_dir):
    src = os.path.join(pituitary_dir, filename)
    dst = os.path.join(new_dir, 'pituitary', filename)
    shutil.move(src, dst)

In [35]:
import os
import shutil
from sklearn.model_selection import train_test_split

# Define function to create directories
def create_dir(path):
    if not os.path.exists(path):
        os.makedirs(path)

# Define function to split data and count images
def split_data(source, train_dest, val_dest, test_dest, test_size=0.1, val_size=0.2):
    # Get all class directories
    classes = [d for d in os.listdir(source) if os.path.isdir(os.path.join(source, d)) and not d.startswith('.')]
    
    counts = {}  # Dictionary to store image counts
    
    for class_name in classes:
        class_dir = os.path.join(source, class_name)
        images = [f for f in os.listdir(class_dir) if os.path.isfile(os.path.join(class_dir, f)) and not f.startswith('.')]
        
        # Split the dataset into train+val and test sets
        train_and_val, test = train_test_split(images, test_size=test_size, random_state=42)
        # Split the train+val dataset into train and val sets
        train, val = train_test_split(train_and_val, test_size=val_size, random_state=42)
        
        counts[class_name] = {
            'train': len(train),
            'val': len(val),
            'test': len(test)
        }
        
        # Copy files to the respective directories
        for img in train:
            create_dir(os.path.join(train_dest, class_name))
            shutil.copy(os.path.join(class_dir, img), os.path.join(train_dest, class_name, img))
        
        for img in val:
            create_dir(os.path.join(val_dest, class_name))
            shutil.copy(os.path.join(class_dir, img), os.path.join(val_dest, class_name, img))
        
        for img in test:
            create_dir(os.path.join(test_dest, class_name))
            shutil.copy(os.path.join(class_dir, img), os.path.join(test_dest, class_name, img))
    
    return counts

# Paths
source_dir = 'dataset'
train_dir = 'output/training'
val_dir = 'output/validation'
test_dir = 'output/testing'

# Split the data and get image counts
image_counts = split_data(source_dir, train_dir, val_dir, test_dir)

# Print image counts
for class_name, count_dict in image_counts.items():
    print(f"Class: {class_name}")
    print(f"  Training: {count_dict['train']} images")
    print(f"  Validation: {count_dict['val']} images")
    print(f"  Testing: {count_dict['test']} images")
    print()


Class: glioma
  Training: 4540 images
  Validation: 1136 images
  Testing: 631 images

Class: meningioma
  Training: 4600 images
  Validation: 1151 images
  Testing: 640 images

Class: normal
  Training: 2207 images
  Validation: 552 images
  Testing: 307 images

Class: pituitary
  Training: 4253 images
  Validation: 1064 images
  Testing: 591 images



# Data Modelling

### ResNet50, Dense121, MobileNetv3

In [ ]:
import tensorflow as tf
tf.config.list_physical_devices('GPU')

In [2]:
tf.debugging.set_log_device_placement(True)

# Create some tensors
a = tf.constant([[1.0, 2.0, 3.0], [4.0, 5.0, 6.0]])
b = tf.constant([[1.0, 2.0], [3.0, 4.0], [5.0, 6.0]])
c = tf.matmul(a, b)

print(c)

Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op MatMul in device /job:localhost/replica:0/task:0/device:GPU:0
tf.Tensor(
[[22. 28.]
 [49. 64.]], shape=(2, 2), dtype=float32)


In [3]:
tf.debugging.set_log_device_placement(True)

# Place tensors on the CPU
with tf.device('/CPU:0'):
  a = tf.constant([[1.0, 2.0, 3.0], [4.0, 5.0, 6.0]])
  b = tf.constant([[1.0, 2.0], [3.0, 4.0], [5.0, 6.0]])

# Run on the GPU
c = tf.matmul(a, b)
print(c)

Executing op MatMul in device /job:localhost/replica:0/task:0/device:GPU:0
tf.Tensor(
[[22. 28.]
 [49. 64.]], shape=(2, 2), dtype=float32)


In [4]:
tf.debugging.set_log_device_placement(True)

try:
  # Specify an invalid GPU device
  with tf.device('/device:GPU:2'):
    a = tf.constant([[1.0, 2.0, 3.0], [4.0, 5.0, 6.0]])
    b = tf.constant([[1.0, 2.0], [3.0, 4.0], [5.0, 6.0]])
    c = tf.matmul(a, b)
except RuntimeError as e:
  print(e)

Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op MatMul in device /job:localhost/replica:0/task:0/device:GPU:0


In [5]:
import tensorflow as tf

gpus = tf.config.experimental.list_physical_devices('GPU')
if gpus:
    try:
        for gpu in gpus:
            tf.config.experimental.set_memory_growth(gpu, True)
    except RuntimeError as e:
        print(e)


Physical devices cannot be modified after being initialized


In [6]:
import tensorflow as tf
import time

# Large matrix multiplication to see GPU usage
with tf.device('/GPU:0'):
    a = tf.random.normal([5000, 5000])
    b = tf.random.normal([5000, 5000])

    start_time = time.time()
    c = tf.matmul(a, b)
    end_time = time.time()

print("Matrix multiplication result:\n", c)
print("Time taken for matrix multiplication on GPU: ", end_time - start_time, "seconds")


Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op RandomStandardNormal in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op Mul in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op AddV2 in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op RandomStandardNormal in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op Mul in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op AddV2 in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op MatMul in device /job:localhost/replica:0/task:0/device:GPU:0
Matrix multiplication result:
 tf.Tensor(
[[ 6.0609100e+01 -3.2065056e+01 -3.7152592e+01 ...  1.1892221e+02
  -4.1967690e+01 -8.4616280

In [7]:
import tensorflow as tf
from tensorflow.keras.applications import MobileNetV3Large, DenseNet121, ResNet50
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from tensorflow.keras.layers import Dense, GlobalAveragePooling2D
from tensorflow.keras.models import Model
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.metrics import AUC
import os
import time

# Create AUC metric instance outside of any tf.function
auc_metric = AUC(curve='PR', name='mAP')

def compute_map(y_true, y_pred):
    # Use the pre-created AUC instance
    return auc_metric(y_true, y_pred)

def build_model(base_model, num_classes):
    # Add custom layers
    x = base_model.output
    x = GlobalAveragePooling2D()(x)
    x = Dense(1024, activation='relu')(x)
    predictions = Dense(num_classes, activation='softmax')(x)

    # Model to train
    model = Model(inputs=base_model.input, outputs=predictions)

    # Freeze the base_model layers
    for layer in base_model.layers:
        layer.trainable = False

    return model

def train_model(model, train_generator, val_generator, test_generator, epochs):
    # Compile the model with mAP metric
    model.compile(optimizer=Adam(), loss='categorical_crossentropy', metrics=['accuracy', compute_map])

    # Record the training start time
    start_time = time.time()

    # Train the model
    history = model.fit(
        train_generator,
        epochs=epochs,
        validation_data=val_generator
    )

    # Calculate training time
    training_time = time.time() - start_time

    # Unfreeze some layers in base_model and fine-tune
    for layer in model.layers[-20:]:  # Fine-tune last 20 layers
        layer.trainable = True

    # Recompile the model
    model.compile(optimizer=Adam(1e-5), loss='categorical_crossentropy', metrics=['accuracy', compute_map])

    # Fine-tune the model
    history_fine = model.fit(
        train_generator,
        epochs=epochs,
        validation_data=val_generator
    )

    # Evaluate the model
    loss, accuracy, mAP = model.evaluate(test_generator)
    print(f'Test accuracy: {accuracy:.2f}, mAP: {mAP:.2f}')
    print(f'Training time: {training_time:.2f} seconds')

    return history, history_fine

Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op Fill in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op VarHandleOp in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op AssignVariableOp in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op Fill in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op VarHandleOp in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op AssignVariableOp in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op Fill in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op VarHandleOp in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op AssignVariableOp in device /job:localh

In [8]:
# Directory setup
source_dir = 'output'
train_dir = os.path.join(source_dir, 'training')
val_dir = os.path.join(source_dir, 'validation')
test_dir = os.path.join(source_dir, 'testing')

# Image data generators
def create_data_generators(train_dir, val_dir, test_dir):
    train_datagen = ImageDataGenerator(
        rescale=1./255,
        rotation_range=40,
        width_shift_range=0.2,
        height_shift_range=0.2,
        shear_range=0.2,
        zoom_range=0.2,
        horizontal_flip=True,
        fill_mode='nearest'
    )

    val_datagen = ImageDataGenerator(rescale=1./255)
    test_datagen = ImageDataGenerator(rescale=1./255)

    train_generator = train_datagen.flow_from_directory(
        train_dir,
        target_size=(224, 224),
        batch_size=32,
        class_mode='categorical'
    )

    val_generator = val_datagen.flow_from_directory(
        val_dir,
        target_size=(224, 224),
        batch_size=32,
        class_mode='categorical'
    )

    test_generator = test_datagen.flow_from_directory(
        test_dir,
        target_size=(224, 224),
        batch_size=32,
        class_mode='categorical'
    )

    return train_generator, val_generator, test_generator


##### MobileNetv3

In [ ]:
# Train MobileNetV3
train_generator, val_generator, test_generator = create_data_generators(train_dir, val_dir, test_dir)
base_model = MobileNetV3Large(weights='imagenet', include_top=False, input_shape=(224, 224, 3))
model = build_model(base_model, len(train_generator.class_indices))
print("\nTraining MobileNetV3Large:")
history_mobilenet, history_fine_mobilenet = train_model(model, train_generator, val_generator, test_generator, epochs=50)

Found 15600 images belonging to 4 classes.
Found 3903 images belonging to 4 classes.
Found 2169 images belonging to 4 classes.
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op StatelessRandomGetKeyCounter in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op StatelessRandomUniformV2 in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op Sub in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op Mul in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op AddV2 in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op VarHandleOp in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op AssignVariableOp in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op Fill in device /job:localhost/replica:0/task:0/

##### Dense121

In [ ]:
# Train DenseNet121
train_generator, val_generator, test_generator = create_data_generators(train_dir, val_dir, test_dir)
base_model = DenseNet121(weights='imagenet', include_top=False, input_shape=(224, 224, 3))
model = build_model(base_model, len(train_generator.class_indices))
print("\nTraining DenseNet121:")
history_densenet, history_fine_densenet = train_model(model, train_generator, val_generator, test_generator, epochs=50)

Found 15600 images belonging to 4 classes.
Found 3903 images belonging to 4 classes.
Found 2169 images belonging to 4 classes.
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op StatelessRandomGetKeyCounter in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op StatelessRandomUniformV2 in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op Sub in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op Mul in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op AddV2 in device /job:localhost/replica:0/task:0/device:GPU:0
Executing op VarHandleOp in device /job:localhost/replica:0/task:

##### ResNet50

In [ ]:
# Train ResNet50
train_generator, val_generator, test_generator = create_data_generators(train_dir, val_dir, test_dir)
base_model = ResNet50(weights='imagenet', include_top=False, input_shape=(224, 224, 3))
model = build_model(base_model, len(train_generator.class_indices))
print("\nTraining ResNet50:")
history_resnet, history_fine_resnet = train_model(model, train_generator, val_generator, test_generator, epochs=50)

# Data Visualization

### Model Loss and Accuracy Graphs

In [ ]:
import matplotlib.pyplot as plt

def plot_training_history(history, history_fine, model_name):
    # Plot training & validation accuracy values
    plt.figure(figsize=(12, 4))
    plt.subplot(1, 2, 1)
    plt.plot(history.history['accuracy'])
    plt.plot(history.history['val_accuracy'])
    plt.plot(history_fine.history['accuracy'])
    plt.plot(history_fine.history['val_accuracy'])
    plt.title(f'{model_name} Accuracy')
    plt.xlabel('Epoch')
    plt.ylabel('Accuracy')
    plt.legend(['Train', 'Val', 'Fine Train', 'Fine Val'], loc='upper left')

    # Plot training & validation loss values
    plt.subplot(1, 2, 2)
    plt.plot(history.history['loss'])
    plt.plot(history.history['val_loss'])
    plt.plot(history_fine.history['loss'])
    plt.plot(history_fine.history['val_loss'])
    plt.title(f'{model_name} Loss')
    plt.xlabel('Epoch')
    plt.ylabel('Loss')
    plt.legend(['Train', 'Val', 'Fine Train', 'Fine Val'], loc='upper left')

    plt.tight_layout()
    plt.show()

# Plot training history for MobileNetV3
plot_training_history(history_mobilenet, history_fine_mobilenet, 'MobileNetV3Large')

# Plot training history for DenseNet121
plot_training_history(history_densenet, history_fine_densenet, 'DenseNet121')

# Plot training history for ResNet50
plot_training_history(history_resnet, history_fine_resnet, 'ResNet50')


In [ ]:
from sklearn.metrics import confusion_matrix, ConfusionMatrixDisplay
import numpy as np

def plot_confusion_matrix(model, generator, class_names):
    # Get true labels and predictions
    true_labels = generator.classes
    pred_labels = model.predict(generator)
    pred_labels = np.argmax(pred_labels, axis=1)

    # Compute confusion matrix
    cm = confusion_matrix(true_labels, pred_labels)
    disp = ConfusionMatrixDisplay(confusion_matrix=cm, display_labels=class_names)

    # Plot confusion matrix
    disp.plot(cmap=plt.cm.Blues)
    plt.show()

# Get class names
class_names = list(train_generator.class_indices.keys())

# Plot confusion matrix for MobileNetV3
plot_confusion_matrix(model, test_generator, class_names)
